# Ch 1: Overview
Welcome fellow traders! 

This is a Notebook on the My_Trading_Buddy. The aim of this project is to provide a assistance to a technical approach to trading on the ASX. The goal is for you to be equipt with the necessary tools to analyse market trends and simulate your personalised model! I have broken this up into chapters like a notebook. 

Best of Luck, 

Your trading buddy :)

## Ch 1.1: Import Packages

In [1]:
import yfinance as yf
import pandas as pd
from pandas_datareader import data as pdr
import matplotlib.pyplot as plt
import math
import numpy as np

import datetime as dt

import plotly.offline as pyo
import plotly

import plotly.graph_objects as go
from plotly.subplots import make_subplots

pyo.init_notebook_mode(connected=True)

## Ch 1.2: Scrapping Data and Stock Overview 

In [2]:
# Define Start and End dates

end = dt.datetime.now()
end = dt.datetime(2019,7,7)
start  = dt.datetime(2016,12,12)

In [3]:
# Define Stocks of interest

stocklist = ['MQG','CBA', 'NAB', 'WBC','BOQ','QAN','VAS']
#stocklist = ['MQG','CBA']
#stocklist = ['QAN','ATEC','VAS','NDQ']
stocks = [i + '.AX' for i in stocklist]

In [4]:
# Use the Daily Opening data
import fix_yahoo_finance as yf
df = yf.Ticker(stocks, start,end)
df_price = df.Open
df = df.Open

# Display Stock Info
import plotly.offline as pyo
pyo.init_notebook_mode(connected = True)
pd.options.plotting.backend = 'plotly'
df.plot()

c:\users\andre\appdata\local\programs\python\python39\lib\site-packages\fix_yahoo_finance\__init__.py:0: DeprecationWarning:



*** `fix_yahoo_finance` was renamed to `yfinance`. ***
Please install and use `yfinance` directly using `pip install yfinance -U`

More information: https://github.com/ranaroussi/yfinance




[*********************100%***********************]  7 of 7 completed


def std_data(data, n = 365, percentage = '50%'):
    data_yr = data[data.index > end - dt.timedelta(days = n)].copy()
    for i in stocks:
        median = data_yr.describe(percentiles=[0.1,0.5,0.9])[i][percentage]
        print(i,median)
        data_yr[i] = data_yr.loc[:,(i)].div(median)
    return data_yr
st = std_data(df)
st.plot()

df['MQG.AX'].pct_change().plot(kind='hist')

## Ch 1.2i: Quick testing algorithm


In [5]:
def final_results(df, stocks = stocks):
    final_array = []
    for stock in stocks:
        final_array.append(round(df[stock][-1],5))
    print('Stocks: ',stocks)
    print('Results:',final_array)
    print('Average: {}'.format(round(sum(final_array)/len(final_array),2)))

## Ch 1.3 Standard Models to Compare 
This section is prebuilt algorithms (from scratch) that are common trading strategies. It is important to compare your proposed model/algorithm against these standards as we want our model to be smarter than the more common trading strategies.

Be sure to use the appropriate Standard model for your assumptions

###  Ch 1.3a Buy and Hold
The Classic buy at the start of your trading period and sell on the last day

This is a very good strategy when you have a large sum of money at the start of your trading period

In [6]:
def buy_n_hold(p_df, start = dt.timedelta(days = 365), end = dt.datetime.now(), n = 0, stocks = ['CBA.AX'], mode = 'value',
            total_investment = None, brokerage_fee = 20):
    if n != 0:
        start = dt.timedelta(days = n)
    #price_df = p_df[p_df.index > end - start].copy()
    price_df = p_df
    df = pd.DataFrame(index = p_df.index)
    new_df = df
    #new_df = df[df.index > end - start].copy()
    
    for stock in stocks:
        initial = price_df[stock][0]
        final = price_df[stock][-1]
        step = (final - initial) / len(new_df)
        value_array = []
        percentage_array = []

        if total_investment != None:
            stock_num = (total_investment - brokerage_fee) / initial
            for day_index in range(len(price_df[stock])):
                current_value = (initial + step * day_index) 
                value_array.append(current_value * stock_num)
                percentage_array.append(((current_value / initial) - 1) * 100)
        elif total_investment == None:
            for day_index in range(len(price_df[stock])):
                current_value = initial + step * day_index
                value_array.append(current_value)
                percentage_array.append(((current_value / initial) - 1) * 100)

        if mode == 'value':
            new_df[stock] = value_array
        elif mode == 'percentage':
            new_df[stock] = percentage_array
    return new_df
bnh = buy_n_hold(p_df = df_price, mode = 'percentage', total_investment = 7000, stocks = stocks, n = 3000)
final_results(bnh)
bnh.plot()

Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
Results: [51.29556, 1.67089, -9.54895, -12.51929, -17.635, 63.16737, 19.91843]
Average: 13.76


### Ch 1.3b Dollar Cost Average
A strict stategy where you input the same fixed value for a specific period. The idea is that you purchase more stocks when the market is down, and purchase less stocks when the market is up.

This strategy is good for investors who have a steady stream of income they want to invest in and if the market is continuously going up

In [7]:
def doll_cost_av(p_df, day_freq = 60, trade_amount = 5000, stocks = ['CBA.AX'], brokerage_fee = 20, 
                 mode = 'value', start = dt.timedelta(days = 365), end = dt.datetime.now(), n = 0):
    if n != 0:
        start = dt.timedelta(days = n)
    df = pd.DataFrame(index = p_df.index)
    #new_df = df[df.index > end - start].copy()
    new_df = df
    #price_df = p_df[p_df.index > end - start].copy()
    price_df = p_df
    inv_amount = 0
    inv_array = []
    inv_counter = 0
    for time_index in price_df[stocks].index:
        # trade on the first day
        if len(inv_array) == 0:
            inv_amount += trade_amount
            inv_array.append(inv_amount)
            inv_counter += 1
        elif inv_counter != day_freq: 
            inv_array.append(inv_amount)
            inv_counter += 1
        elif inv_counter == day_freq:
            inv_amount += trade_amount
            inv_array.append(inv_amount)
            inv_counter = 0
    #print(inv_array)
    new_df['invested'] = inv_array

    # dollar cost average
    for stock in stocks:
        price_amount = 0
        price_array = []
        day_counter = 0
        stock_amount = 0
        value_delta_array = []
        for time_index in price_df[stocks].index:
            if len(price_array) == 0:
                price_amount += trade_amount
                #print(stock,time_index,price_df[stock][time_index])
                stock_amount += (trade_amount- brokerage_fee) / price_df[stock][time_index]
                price_array.append(price_amount)
                value_delta_array.append(0)
                day_counter += 1
            elif day_counter != day_freq: 
                price_array.append(stock_amount * price_df[stock][time_index])
                value_delta_array.append(stock_amount * price_df[stock][time_index] - new_df['invested'][time_index])
                day_counter += 1
            elif day_counter == day_freq:
                price_amount += trade_amount
                stock_amount += (trade_amount- brokerage_fee) / price_df[stock][time_index]
                price_array.append(stock_amount * price_df[stock][time_index])
                value_delta_array.append(stock_amount * price_df[stock][time_index] - new_df['invested'][time_index])
                day_counter = 0
            #print(price_amount)
            
        if mode == 'percentage':
            new_df[stock] = ((price_array / new_df['invested']) -1 )* 100 
        elif mode == 'value':
            new_df[stock] = price_array
        elif mode == 'value_delta':
            new_df[stock] = value_delta_array
    if mode == 'percentage' or mode == 'value_delta':
        new_df.drop(columns=['invested'], inplace=True)
    
    return new_df

dca = doll_cost_av(p_df = df_price, mode = 'value_delta', stocks = stocks)
final_results(dca)
#print(dca)
dca.plot()

Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
Results: [14138.29613, 4730.23767, -2107.88642, -2537.15422, -7542.9316, 4271.19899, 6830.57188]
Average: 2540.33


## Ch 1.4: Compare Algorythms

In [8]:
def compare_results(df1, df2, stocks = ['CBA.AX']):
    results_array = []
    for stock in stocks:
        df1_result = df1[stock][-1]
        df2_result = df2[stock][-1]
        difference = (df1_result - df2_result) 
        results_array.append(difference)
        print('Stock: {}, {}%'.format(stock, round(difference,2)))
    print('Average result: {}%'.format(round(sum(results_array)/len(results_array),2)))


n = 365
mode = 'percentage'

bnh = buy_n_hold(p_df = df_price, mode = mode, n = n, stocks = stocks, total_investment = 8000)
dca = doll_cost_av(p_df = df_price, mode = mode, n = n, stocks = stocks)
compare_results(df1 = bnh, df2 = dca, stocks = stocks)

Stock: MQG.AX, 25.59%
Stock: CBA.AX, -6.93%
Stock: NAB.AX, -5.72%
Stock: WBC.AX, -7.91%
Stock: BOQ.AX, -3.92%
Stock: QAN.AX, 55.4%
Stock: VAS.AX, 7.5%
Average result: 9.15%


In [9]:
# Need to finish this
def compare_graphs(df1, df2):
    

IndentationError: expected an indented block (<ipython-input-9-4deaffb38f31>, line 3)

# Ch 2: Building a New Algorithm

## Ch 2.1: First Algorithm
We standardise each stock performance by dividing it by the rolling median/mean (so we can compare each stock). 

Realising the area under this transformed graph is a better indicator for stock market value. This shows the overall growth of the stock.

Since stock values a year ago is less important information for us than stock values last week, we must include a reduction factor.

We will then put a make a threshold for the new graph and determine when to trade.

In [10]:
# Inputs: df with stock prices
# Outputs a rolling normalised df for all stocks

# Normalises using a rolling median
def norm_df_med(df, window = 30, stocks = ['CBA.AX']):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = (df[stock] / df[stock].rolling(window, min_periods = 0).median() -1)
    return new_df

# Normalises using rolling mean
def norm_df_mean(df, window = 30,  stocks = ['CBA.AX']):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = df[stock] / df[stock].rolling(window, min_periods = 0).mean()-1
    return new_df

df_1 = norm_df_med(df,window = 20, stocks = stocks)

In [11]:
# Inputs: normalised stock prices df
# Outputs: area under the graph with a reduction factor df

def norm_sum_df(df, reduction_factor  = 1 , stocks = ['CBA.AX']):
    new_df = pd.DataFrame(index = df.index)
    for stock in stocks:
        totals = []
        rolling_sum = 0
        for time_index in df.index:
            rolling_sum = (rolling_sum * reduction_factor + df[stock][time_index])
            totals.append(rolling_sum)
        new_df[stock] = totals
    return new_df
df_2 = norm_sum_df(df_1, 0.9, stocks = stocks)
#print(df_2)

In [12]:
# Input: 2 dfs, the first being the transformed df and another being the df with pricing
#        can also input upper and lower threshholds

# Output: df that determines to trade or not based on threshholds
#         also outputs stock price for each given day

def trade_list(df = df, df_price = df_price, start = dt.timedelta(days = 1500), end = dt.datetime.now(), 
               stock = 'CBA.AX', up_thresh = 0.9, low_thresh = 0.25, thresh_window = 180,
              trig_thresh = 20):
    #trim_df = df[df.index > end - start]
    trim_df = df
    n_df = df
    #trim_df_price = df_price[df_price.index > end - start]
    trim_df_price = df_price
    #n_df = (trim_df)

    new_df = pd.DataFrame(index = n_df.index)
    new_df['price'] = trim_df_price[stock]
    new_df['norm'] = n_df[stock]
    new_df['up_bound'] = df[stock].rolling(thresh_window, min_periods = 0).quantile(up_thresh).copy()
    new_df['low_bound'] = df[stock].rolling(thresh_window, min_periods = 0).quantile(low_thresh).copy()
    
    trade = []
    buy_trig, sell_trig = 0, 0   
    cooler_counter = 0
    for i in n_df.index:
        if n_df[stock][i] > new_df['up_bound'][i] and sell_trig == 0 and cooler_counter > 10:
            sell_trig = 1
            trade.append(1)
        elif n_df[stock][i] < new_df['low_bound'][i] and buy_trig == 0 and cooler_counter > 10:
            buy_trig = 1
            trade.append(-1)
        else:
            trade.append(0)
        cooler_counter+=1
        
        #Triggers for sell
        if sell_trig < trig_thresh and sell_trig > 0:
            sell_trig += 1
        elif sell_trig == trig_thresh:
            sell_trig = 0
            
        #Triggers for buy
        if buy_trig < trig_thresh and buy_trig > 0:
            buy_trig += 1
        elif buy_trig == trig_thresh:
            buy_trig = 0 
            
    new_df['trade'] = trade
    return new_df

In [13]:
def trading_results(df, amount_per_trade = 8000, bank = 20000, brokerage_fee = 20):
    holding_stocks = 0
    bank_value = []
    total_value = []
    amount_per_trade = 1 * bank
    for date_index in df.index:
        if (df['trade'][date_index] == -1) & (bank >= amount_per_trade):
            # print('buy')
            bank += - amount_per_trade
            holding_stocks += (amount_per_trade - brokerage_fee) / df['price'][date_index]
            amount_per_trade = 1* bank
        elif (df['trade'][date_index] == 1) and (holding_stocks > 0):
            # print('sell')
            bank += holding_stocks * df['price'][date_index] - brokerage_fee
            holding_stocks = 0
            amount_per_trade = 1 * bank
        bank_value.append(bank)
        
        if math.isnan(df['price'][date_index]) == True:
            total_value.append(bank)
        else:
            total_value.append(bank + holding_stocks * int(df['price'][date_index]))
    
    # Must sell all stocks on last day (today)
    last_index = -1
    while math.isnan(df['price'][last_index]) == True:
        last_index += -1
    else:
        bank_value[-1] = bank + holding_stocks * int(df['price'][last_index])
    df['bank_value'] = bank_value
    df['total_value'] = total_value
    return df

NameError: name 'test_90' is not defined

In [18]:
df_1yr_norm = norm_df_med(df, window = 45, stocks = stocks)
test_90 = norm_sum_df(df_1yr_norm, stocks = stocks, reduction_factor = 0.9)
fig_test = make_subplots(rows = 1, cols = 1)
finish = []
trading_df = pd.DataFrame(index = test_90.index)
results_df = pd.DataFrame(index = test_90.index)
wallet_df = pd.DataFrame(index = test_90.index)
#delay_days = 360

for i in stocks:
    print(i)
    a = trade_list(test_90, stock = i, start = start, end =  end, low_thresh = 0.05, up_thresh = 0.60, thresh_window = 30)
    bnk = 8000
    results = trading_results(a, amount_per_trade = 8000, bank = bnk, brokerage_fee = 20)
    results_df[i] = results['trade']
    finish.append(round(((results['bank_value'][-1]/bnk)-1)*100, 6))
    trading_df[i] = ((results['bank_value']/bnk)-1)*100
    fig_test.add_trace(go.Scatter(x=a.index, y = ((results['bank_value']/bnk)-1)*100,  name = i), row =1, col = 1)
    
    wallet_df[i] = results['bank_value']
    
fig_test.show()
print(stocks)
print(finish)


cols = plotly.colors.DEFAULT_PLOTLY_COLORS
k=0
fig_norm_comp = make_subplots(rows = 5, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('Bank Stocks','Normalised Stocks, 90', 'Results','Trading', 'Bank Total'),
                   row_width = [1,1,1,1,1])

total_wallet = []
for i in wallet_df.index:
    total_wallet.append(sum(sum(wallet_df[wallet_df.index == i].values)))
wallet_df['running_total'] = total_wallet
#wallet_df['running_total'].plot()

for i in df_1yr_norm:
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = df[i], name = i,
                                       legendgroup = i, marker=dict(color=cols[k])), row =1, col = 1)
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = test_90[i], name = i, 
                                       showlegend = False, legendgroup = i, marker=dict(color=cols[k])), row =2, col = 1)    
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = results_df[i], name = i, 
                                       showlegend = False, legendgroup = i, marker=dict(color=cols[k])), row =3, col = 1)
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = trading_df[i], name = i, 
                                       showlegend = False, legendgroup = i, marker=dict(color=cols[k])), row =4, col = 1)
    k += 1
print(sum(finish)/len(finish))

fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = wallet_df['running_total'], name = 'running_total', 
                                       showlegend = True, legendgroup = 'running_total', marker=dict(color=cols[k])), row =5, col = 1)


fig_norm_comp.show()


MQG.AX
CBA.AX
NAB.AX
WBC.AX
BOQ.AX
QAN.AX
VAS.AX


['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
[33.014309, -3.218632, -7.002964, -1.967952, -9.973639, 22.921346, 1.835251]
5.086816999999999


In [518]:
bnh = buy_n_hold(p_df = df_price, mode = 'percentage', total_investment = 8000, stock_list = stocks)
bnh_finish = []
df_5_finish = []
for i in stocks:
    #print('Stock {}: {}%'.format(i, round(bnh[i][-1],2)))
    bnh_finish.append(round(bnh[i][-1],6))
    df_5_finish.append(round(df_5[i][-1],6))

print('Stocks name ', stocks)
print('My Algorythm', finish)
print('BnH standard', bnh_finish)
stats_comparison = []
for i in range(len(bnh_finish)):
    stats_comparison.append(round(finish[i] - bnh_finish[i],6))
print('Difference  ',stats_comparison)
print('Average:    ', round(sum(stats_comparison)/len(stats_comparison),2),'%')

Stocks name  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
My Algorythm [19.616626, 8.839914, -3.47727, 4.250539, -2.203429, 24.528326, 1.909405]
BnH standard [51.295558, 1.670892, -9.548949, -12.519288, -17.634996, 63.167366, 19.918434]
Difference   [-31.678932, 7.169022, 6.071679, 16.769827, 15.431567, -38.63904, -18.009029]
Average:     -6.13 %


In [455]:
wallet_df['running_total'].plot()
fin = wallet_df['running_total'][-1]/(bnk*len(stocks))
most = wallet_df['running_total'].max()/(bnk*len(stocks))
least = wallet_df['running_total'].min()/(bnk*len(stocks))
print(fin,most,least)

1.1408668729017302 1.1495497740117915 0.0


######## For Macquarie 
stocks = ['MQG.AX']#, 'MQG.AX']
df_1 = norm_df_mean(df, window = 20)
df_2 = norm_df_sum(df_1, reduction_factor = 0.95, n = 365)
testing_graph = make_subplots(rows = 1, cols = 1,
                    subplot_titles = ('Testing Group'))
k = 0
for i in stocks:
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_1[i]*8, name = i+'gradient', 
                                       showlegend = True, legendgroup = i+'gradient', marker=dict(color=cols[k])))
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_2[i], name = i + 'Area', 
                                       showlegend = True, legendgroup = i + 'Area', marker=dict(color=cols[k+5])))
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_price[i]*0.01, name = i+'price', 
                                       showlegend = True, legendgroup = i+'price', marker=dict(color=cols[k+2])))
    k+=1
testing_graph.show()

## Standard Trading Strategies

 I am unsure whether my designed trading strategy is effective (sometimes the trading season is strong, leading to strong trading simulations. Sometimes the trading season is weak, leading to bad trading seasons), so I devise two models to compare our trading algorithm against:
 1. Buy_n_sell: Buy a fixed amount at the start of a period and hold onto it with no buying or selling in between.
 2. Dollar Cost Average: Purchase shares in fixed time interval with a fixed cap of money

It is good to note, both these algorythms are strong in a uniformly increasing market which is not the case in the current market (Jan 2023)

###################### This is a working copy
def trading_results(df, amount_per_trade = 8000, bank = 20000, brokerage_fee = 20):
    holding_stocks = 0
    total_value = []
    for i in df.index:
        if (df['trade'][i] == -1) & (bank >= amount_per_trade):
            # print('buy')
            bank += -amount_per_trade
            holding_stocks += (amount_per_trade - brokerage_fee) / df['price'][i]
        elif (df['trade'][i] == 1) and (holding_stocks > 0):
            # print('sell')
            bank += holding_stocks * df['price'][i] - brokerage_fee
            holding_stocks = 0
        total_value.append(bank)
    
    total_value[-1] = bank + holding_stocks * int(df['price'][-1])
    df['value'] = total_value
    return df

#norm_df_med(df, window = 30).plot()
df_1yr = df[df.index > end - dt.timedelta(days = 3000)]
df_1yr_norm = norm_df_med(df_1yr,window = 30)

cols = plotly.colors.DEFAULT_PLOTLY_COLORS
k=0
fig_norm_comp = make_subplots(rows = 3, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('Bank Stocks','Normalised Stocks'),
                   row_width = [0.5,0.5,0.5])
test = norm_df_sum(df_1yr_norm)
for i in df_1yr:
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr.index, y = df_1yr[i], name = i, 
                                       legendgroup = i, marker=dict(color=cols[k])), row =1, col = 1)
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = test[i], name = i, 
                                       showlegend = False, legendgroup = i, marker=dict(color=cols[k])), row =2, col = 1)
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = df_1yr_norm[i], name = i, 
                                       showlegend = False, legendgroup = i, marker=dict(color=cols[k])), row =3, col = 1)
    k += 1
fig_norm_comp

## Ch 2.2: Second Algorithm
We will use the standardised rolling median as well as the integral function to work out the best trading pattern.

Using the rolling median graph as the gradient, we can determine when the graph intercepts with the horizontal axis and thus finding the dip of the area graph. Once that has occured we need to set a threshold for the area graph beyond which will trade to remove any uneccesary trades

In [68]:
def norm_int_df(norm_df, stocks = ['CBA.AX']):
    new_df = pd.DataFrame(index = norm_df.index)
    for stock in stocks:
        crossing_array = []
        for time_index in range(len(norm_df[stock])):
            if time_index == 0:
                crossing_array.append(0)
            elif norm_df[stock][time_index - 1] < 0 and norm_df[stock][time_index] >= 0:
                # indicate to buy
                crossing_array.append(-1)
            elif norm_df[stock][time_index - 1] >= 0 and norm_df[stock][time_index] < 0:
                # indicate to sell
                crossing_array.append(1)
            else: 
                crossing_array.append(0)
        new_df[stock] = crossing_array
    return new_df
df_3 = norm_int_df(df_1, stocks = stocks)
df_3.plot()          



def decision_trade_df(norm_int_df = df, norm_sum_df = df, threshold = 0.5, stocks = ['CBA.AX'],
                     trig_thresh = 20):
    new_df = pd.DataFrame(index = norm_int_df.index)
    for stock in stocks:
        trade_array = []
        upper_limit, lower_limit = 0,0
        buy_trig, sell_trig, cooler_counter = 0, 0, 0
        for time_index in range(len(norm_int_df)):
            if norm_int_df[stock][time_index] == 1 and norm_sum_df[stock][time_index] > threshold * upper_limit and sell_trig == 0 and cooler_counter > 5:
                upper_limit = norm_sum_df[stock][time_index]
                trade_array.append(1)
                sell_trig = 1
            elif norm_int_df[stock][time_index] == -1 and norm_sum_df[stock][time_index] < threshold * lower_limit and buy_trig == 0 and cooler_counter > 5:
                lower_limit = norm_sum_df[stock][time_index]
                trade_array.append(-1)
                buy_trig = 1
            else:
                trade_array.append(0)
            
            cooler_counter += 1
               
            #Triggers for sell
            if sell_trig < trig_thresh and sell_trig > 0:
                sell_trig += 1
            elif sell_trig == trig_thresh:
                sell_trig = 0

            #Triggers for buy
            if buy_trig < trig_thresh and buy_trig > 0:
                buy_trig += 1
            elif buy_trig == trig_thresh:
                
                buy_trig = 0 
        new_df[stock] = trade_array
    return(new_df)
#print(df_2)
df_4 = decision_trade_df(norm_int_df = df_3, norm_sum_df = df_2, stocks = stocks)
df_4.plot()

In [191]:
# Input: intercept indicator df and normalised area df
# Output: trade df 
# Gradient = 0, check area graph if its large enough, then buy/sell

def decision_trade_df(norm_int_df = df, norm_sum_df = df, limit_factor = 1, stocks = ['CBA.AX'],
                     trig_thresh = 20):
    new_df = pd.DataFrame(index = norm_int_df.index)
    for stock in stocks:
        trade_array = []
        pos_limit, neg_limit = [],[]
        upper_limit, lower_limit = 0,0
        buy_trig, sell_trig, cooler_counter = 0, 0, 0
        for time_index in range(len(norm_int_df)):
            if norm_sum_df[stock][time_index] >= 0:
                pos_limit.append(norm_sum_df[stock][time_index])
                upper_limit = sum(pos_limit)/len(pos_limit)
            elif norm_sum_df[stock][time_index] < 0:
                neg_limit.append(norm_sum_df[stock][time_index])
                lower_limit = sum(neg_limit)/len(neg_limit)
                
            #print(upper_limit,lower_limit)
            if norm_int_df[stock][time_index] == 1 and norm_sum_df[stock][time_index] > limit_factor * upper_limit and sell_trig == 0 and cooler_counter > 5:
                upper_limit = norm_sum_df[stock][time_index]
                trade_array.append(1)
                sell_trig = 1
            elif norm_int_df[stock][time_index] == -1 and norm_sum_df[stock][time_index] < limit_factor * lower_limit and buy_trig == 0 and cooler_counter > 5:
                lower_limit = norm_sum_df[stock][time_index]
                trade_array.append(-1)
                buy_trig = 1
            else:
                trade_array.append(0)
            
            cooler_counter += 1
               
            #Triggers for sell
            if sell_trig < trig_thresh and sell_trig > 0:
                sell_trig += 1
            elif sell_trig == trig_thresh:
                sell_trig = 0

            #Triggers for buy
            if buy_trig < trig_thresh and buy_trig > 0:
                buy_trig += 1
            elif buy_trig == trig_thresh:
                
                buy_trig = 0 
        new_df[stock] = trade_array
    return(new_df)
#print(df_2)
df_4 = decision_trade_df(norm_int_df = df_3, norm_sum_df = df_2, stocks = stocks)
df_4.plot()

In [219]:
def trade_price_df(price_df = df_price, decision_trade_df = df, brokerage_fee = 20, 
                   trade_amount = 6000, compound_factor = None, bank = 8000, mode = 'percentage',
                  stocks = ['CBA.AX']):
    bank_initial = bank
    print('Trade Output:', mode)
    #print(decision_trade_df)
    new_df = pd.DataFrame(index = decision_trade_df.index)

    #if trade_amount > 10000:
    #    brokerage_fee = 30
    for stock in stocks:
        bank = bank_initial
        if compound_factor != None:
            trade_amount = compound_factor * bank
        holding_stocks = 0
        bank_value = []
        total_value = []
        for date_index in decision_trade_df[stock].index:
            if (decision_trade_df[stock][date_index] == -1) & (bank >= trade_amount): 
                # print('buy')
                bank += - trade_amount
                holding_stocks += (trade_amount - brokerage_fee) / price_df[stock][date_index]
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            elif (decision_trade_df[stock][date_index] == 1) and (holding_stocks > 0):
                # print('sell')
                bank += holding_stocks * price_df[stock][date_index] - brokerage_fee
                holding_stocks = 0
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            bank_value.append(bank)
            
            if math.isnan(price_df[stock][date_index]) == True:
                total_value.append(bank)
            else:
                total_value.append(bank + holding_stocks * int(price_df[stock][date_index]))
        last_index = -1
        while math.isnan(price_df[stock][last_index]) == True:
            last_index += -1
        else:
            bank_value[-1] = bank + holding_stocks * int(price_df[stock][last_index])
            #print(stock,bank_value[-21],bank_value[-1])
        
        if mode == 'value':
            new_df[stock] = bank_value
        elif mode == 'bank':
            new_df[stock] = total_value
        elif mode == 'percentage':
            new_df[stock] = ((np.array(total_value) / bank_initial) -1) * 100
    return(new_df)
stocks = [i + '.AX' for i in stocklist]

df_5 = trade_price_df(price_df = df_price, decision_trade_df = df_4, stocks = stocks, mode = 'value')
df_5.plot()

Trade Output: value


In [198]:
#This is a test
stocks = [i + '.AX' for i in stocklist]
sample = norm_df_med(df, window = 60, stocks = stocks)
df_2 = norm_sum_df(df_1, reduction_factor = 0.95, stocks = stocks)
df_3 = norm_int_df(df_1, stocks = stocks)
df_4 = decision_trade_df(norm_int_df = df_3, norm_sum_df = df_2,stocks = stocks, limit_factor = 1, trig_thresh = 20)
df_5 = trade_price_df(price_df = df_price, decision_trade_df = df_4,stocks = stocks, mode = 'value', compound_factor = 1, brokerage_fee = 20)
#df_1.plot()

df_5_finish = []
for i in stocks:    
    df_5_finish.append(round(df_5[i][-1],6))
print(stocks)
print(df_5_finish)
print(round(sum(df_5_finish)/len(df_5_finish)/80,2), '%')
df_5.plot()

Trade Output: value
MQG.AX 8899.839115694876 9026.786699376325
CBA.AX 7499.89289707026 7499.89289707026
NAB.AX 0.0 7491.006730908668
WBC.AX 7251.462474753823 7251.462474753823
BOQ.AX 0.0 6911.52078345856
QAN.AX 0 7468.717108466739
VAS.AX 9234.563844517816 9234.563844517816
['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
[9026.786699, 7499.892897, 7491.006731, 7251.462475, 6911.520783, 7468.717108, 9234.563845]
98.01 %


In [183]:
#This works well
stocks = [i + '.AX' for i in stocklist]
df_1 = norm_df_med(df, window = 60, stocks = stocks)
df_2 = norm_sum_df(df_1, reduction_factor = 0.95, stocks = stocks)
df_3 = norm_int_df(df_1, stocks = stocks)
df_4 = decision_trade_df(norm_int_df = df_3, norm_sum_df = df_2,stocks = stocks, limit_factor = 1, trig_thresh = 20)
df_5 = trade_price_df(price_df = df_price, decision_trade_df = df_4,stocks = stocks, mode = 'value', compound_factor = 1, brokerage_fee = 20)
#df_1.plot()

df_5_finish = []
for i in stocks:    
    df_5_finish.append(round(df_5[i][-1],6))
print(stocks)
print(df_5_finish)
print(round(sum(df_5_finish)/len(df_5_finish)/80,2), '%')
df_5.plot()

0.0 0
0.0010219156307025301 0
0.0036983449766921843 0
0.008509137427442116 0
0.014290832437995473 0
0.019473776550973834 0
0.024258330794886762 0
0.027451277066568133 0
0.028766570532614406 0
0.029484636703571827 0
0.029898298527145397 0
0.030388131406545 0
0.030982395138344946 0
0.03146610882511423 0
0.03181291602642319 0
0.032448851388841404 0
0.03298069119496202 0
0.03370677703021438 0
0.035053948382767784 0
0.03644411990834731 0
0.03691499022988283 0
0.036546208979906944 0
0.035520150419030304 0
0.035520150419030304 -0.009159708492054115
0.035520150419030304 -0.02662018490874387
0.035520150419030304 -0.038979846750887885
0.035520150419030304 -0.051498102407621996
0.035520150419030304 -0.06273231867655839
0.035520150419030304 -0.07512848109320001
0.035520150419030304 -0.08677179027596763
0.035520150419030304 -0.09739888759785556
0.035520150419030304 -0.10635541063272692
0.035520150419030304 -0.11557686833834116
0.035520150419030304 -0.12502585710018208
0.035520150419030304 -0.133431

0.11091206780824173 -0.001054775521974749
0.11184471053895861 -0.001054775521974749
0.11244675045492193 -0.001054775521974749
0.11317573775329416 -0.001054775521974749
0.11388413122953196 -0.001054775521974749
0.11462537056557591 -0.001054775521974749
0.11531116957932637 -0.001054775521974749
0.11595721765240971 -0.001054775521974749
0.11651012779230123 -0.001054775521974749
0.11710659138276786 -0.001054775521974749
0.11785493144560627 -0.001054775521974749
0.11869261004193148 -0.001054775521974749
0.11960855828064272 -0.001054775521974749
0.12069423502095375 -0.001054775521974749
0.12187465311403038 -0.001054775521974749
0.12306705525135321 -0.001054775521974749
0.12425135311676787 -0.001054775521974749
0.12522729809883254 -0.001054775521974749
0.12589780781836973 -0.001054775521974749
0.12635814862141945 -0.001054775521974749
0.1265827080492884 -0.001054775521974749
0.12675380918359044 -0.001054775521974749
0.12713846767699316 -0.001054775521974749
0.1278354165592627 -0.0010547755219

0.1563482642838581 -0.00248003213998761
0.16088903159505863 -0.00248003213998761
0.16595086959085376 -0.00248003213998761
0.17133525122624704 -0.00248003213998761
0.1769208179750086 -0.00248003213998761
0.1826317497386653 -0.00248003213998761
0.1885804259407065 -0.00248003213998761
0.1949109837840549 -0.00248003213998761
0.20171539398595537 -0.00248003213998761
0.20899468838834953 -0.00248003213998761
0.2166096488490343 -0.00248003213998761
0.2242516980467657 -0.00248003213998761
0.2317960646321409 -0.00248003213998761
0.23897893233352194 -0.00248003213998761
0.24572464659662585 -0.00248003213998761
0.25210237409515607 -0.00248003213998761
0.25803271892711044 -0.00248003213998761
0.26345781957618747 -0.00248003213998761
0.26841811386985437 -0.00248003213998761
0.2728794964613295 -0.00248003213998761
0.2770990454249961 -0.00248003213998761
0.28133598526974873 -0.00248003213998761
0.2857090340595405 -0.00248003213998761
0.29026469886570183 -0.00248003213998761
0.29485724006479574 -0.0024

0.3228849869744947 -0.02922980696491495
0.32619249024455066 -0.02922980696491495
0.3289770577573807 -0.02922980696491495
0.33137957815529917 -0.02922980696491495
0.3334988076777407 -0.02922980696491495
0.33532116594440364 -0.02922980696491495
0.3370455034875838 -0.02922980696491495
0.33864732403414655 -0.02922980696491495
0.3402582719391671 -0.02922980696491495
0.3418734720413325 -0.02922980696491495
0.34341290424510995 -0.02922980696491495
0.34482431623334214 -0.02922980696491495
0.34598195439451895 -0.02922980696491495
0.3466827381320555 -0.02922980696491495
0.346957353183104 -0.02922980696491495
0.34678936722718595 -0.02922980696491495
0.3456691503962479 -0.02922980696491495
0.34386294932774103 -0.02922980696491495
0.34134947644157326 -0.02922980696491495
0.33817335284402106 -0.02922980696491495
0.3346470840319539 -0.02922980696491495
0.3346470840319539 -0.029149337128965593
0.3346470840319539 -0.034931183460518905
0.3346470840319539 -0.04468445631629535
0.3346470840319539 -0.057668

0.1731843558945991 -0.19430211938121178
0.17148710973168027 -0.19430211938121178
0.16929153261397836 -0.19430211938121178
0.16929153261397836 -0.1906700443181617
0.16929153261397836 -0.18869619789916967
0.16929153261397836 -0.18792186954961834
0.16929153261397836 -0.18804579950145808
0.16929153261397836 -0.18886984437390558
0.16929153261397836 -0.19046793702371725
0.16929153261397836 -0.19308209942472962
0.16929153261397836 -0.19681258558776524
0.16929153261397836 -0.20166500184464956
0.16929153261397836 -0.20733909496816294
0.16929153261397836 -0.21365178995187456
0.16929153261397836 -0.22005015853570456
0.16929153261397836 -0.2266321135234754
0.16929153261397836 -0.2334346096102142
0.16929153261397836 -0.2404105976381247
0.16929153261397836 -0.24750390924464966
0.16929153261397836 -0.254774346346326
0.16929153261397836 -0.2624641388703124
0.16929153261397836 -0.27026853951630714
0.16929153261397836 -0.2782434789668902
0.16929153261397836 -0.2861937580486865
0.16929153261397836 -0.293

1.1393615639675363 -0.01979380953574627
1.1639108798212074 -0.01979380953574627
1.1887015111478574 -0.01979380953574627
1.213380008721861 -0.01979380953574627
1.2380468128661848 -0.01979380953574627
1.2625250748424142 -0.01979380953574627
1.2868700182091686 -0.01979380953574627
1.3111497889916182 -0.01979380953574627
1.3352676729915378 -0.01979380953574627
1.3591363177066675 -0.01979380953574627
1.3825735058340427 -0.01979380953574627
1.405294165408274 -0.01979380953574627
1.4273433999928014 -0.01979380953574627
1.448767389993302 -0.01979380953574627
1.4695860467063886 -0.01979380953574627
1.4898564742593434 -0.01979380953574627
1.5095074921438865 -0.01979380953574627
1.5285857451410783 -0.01979380953574627
1.5473590941332191 -0.01979380953574627
1.5656862362385033 -0.01979380953574627
1.5836132926503173 -0.01979380953574627
1.601192633689877 -0.01979380953574627
1.6183316532144127 -0.01979380953574627
1.6349550552356593 -0.01979380953574627
1.651086335673768 -0.01979380953574627
1.666

0.17035556100165075 -0.006701864273858308
0.16912861204463198 -0.006701864273858308
0.16778400168881336 -0.006701864273858308
0.16778400168881336 -0.006973583463665332
0.16778400168881336 -0.010917420927898406
0.16778400168881336 -0.016854741681797094
0.16778400168881336 -0.02327690287807089
0.16778400168881336 -0.0286959319188149
0.16778400168881336 -0.03305177866980876
0.16778400168881336 -0.03693502775263616
0.16778400168881336 -0.040158082048104074
0.16778400168881336 -0.042691367271187386
0.16778400168881336 -0.04582373525667784
0.16778400168881336 -0.04957311109616056
0.16778400168881336 -0.0534151769206547
0.16778400168881336 -0.057218820485451606
0.16778400168881336 -0.06096601395608967
0.16778400168881336 -0.06479168991387525
0.16778400168881336 -0.06791770027482986
0.16778400168881336 -0.07061981542200241
0.16778400168881336 -0.07276093091640445
0.16778400168881336 -0.0749903997223712
0.16778400168881336 -0.07691586909744645
0.16778400168881336 -0.07870802518862288
0.16778400

MQG.AX 8899.839115694876 9026.786699376325
CBA.AX 7499.89289707026 7499.89289707026
NAB.AX 0.0 7491.006730908668
WBC.AX 7251.462474753823 7251.462474753823
BOQ.AX 0.0 6911.52078345856
QAN.AX 0 7468.717108466739
VAS.AX 9234.563844517816 9234.563844517816
['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
[9026.786699, 7499.892897, 7491.006731, 7251.462475, 6911.520783, 7468.717108, 9234.563845]
98.01 %


df_2.plot()

df_3.plot()

df_4.plot()

In [550]:
stocks = ['BOQ.AX']#, 'MQG.AX']
#df_1 = norm_df_med(df, window =20)
#df_2 = norm_df_sum(df_1, reduction_factor = 0.9, n = 365)
testing_graph = make_subplots(rows = 1, cols = 1,
                    subplot_titles = ('Testing Group'))
cols = plotly.colors.DEFAULT_PLOTLY_COLORS
k = 0
for i in stocks:
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_1[i] * 8, name = i+' gradient', 
                                       showlegend = True, legendgroup = i+' gradient', marker=dict(color=cols[k])))
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_2[i]*1.5, name = i + ' Area', 
                                       showlegend = True, legendgroup = i + ' Area', marker=dict(color=cols[k+1])))
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_price[i]*0.08, name = i+' price', 
                                       showlegend = True, legendgroup = i+' price', marker=dict(color=cols[k+2])))
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_3[i], name = i+' int', 
                                      showlegend = True, legendgroup = i+' int', marker=dict(color=cols[k+3])))
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_4[i], name = i+' trade', 
                                      showlegend = True, legendgroup = i+' trade', marker=dict(color=cols[k+4])))
    k+=1
testing_graph.show()

df_5.plot()

In [466]:
bnh = buy_n_hold(p_df = df_price, mode = 'percentage', total_investment = 8000, stock_list = stocks)
bnh_finish = []
df_5_finish = []
for i in stocks:
    #print('Stock {}: {}%'.format(i, round(bnh[i][-1],2)))
    bnh_finish.append(round(bnh[i][-1],6))
    df_5_finish.append(round(df_5[i][-1],6))

print('Stocks name ', stocks)
print('My Algorythm', df_5_finish)
print('BnH standard', bnh_finish)
stats_comparison = []
for i in range(len(bnh_finish)):
    stats_comparison.append(round(df_5_finish[i] - bnh_finish[i],6))
print('Difference  ',stats_comparison)
print('Average:    ', round(sum(stats_comparison)/len(stats_comparison),2),'%')

Stocks name  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
My Algorythm [25.578987, -16.71909, -5.714175, -5.833374, -17.155973, -16.059714, -0.588968]
BnH standard [51.295558, 1.670892, -9.548949, -12.519288, -17.634996, 63.167366, 19.918434]
Difference   [-25.716571, -18.389982, 3.834774, 6.685914, 0.479023, -79.22708, -20.507402]
Average:     -18.98 %


In [154]:
df['WBC.AX'].plot()

In [237]:
#norm_sum_df(norm_df_med(df, window = 60, stocks = stocks),stocks = stocks, reduction_factor = 0.9)['WBC.AX'].plot()
gradient = norm_df_med(df,stocks = stocks, window = 20)
gradient['WBC.AX'].plot()
intercepts = norm_int_df(gradient, stocks = stocks)
intercepts['WBC.AX'].plot()
decide = decision_trade_df(norm_int_df = intercepts, norm_sum_df = integral, stocks = stocks, limit_factor = .8)
decide['WBC.AX'].plot()

In [238]:
integral = norm_sum_df(gradient, stocks = stocks, reduction_factor = 0.9)
integral['WBC.AX'].plot()

In [242]:
pricing = trade_price_df(price_df = df_price, decision_trade_df = decide, stocks = stocks, mode = 'percentage')
print(pricing)
pricing['WBC.AX'].plot()


Trade Output: percentage
               MQG.AX     CBA.AX    NAB.AX     WBC.AX    BOQ.AX    QAN.AX  \
Date                                                                        
2016-12-12   0.000000   0.000000  0.000000   0.000000  0.000000  0.000000   
2016-12-13   0.000000   0.000000  0.000000   0.000000  0.000000  0.000000   
2016-12-14   0.000000   0.000000  0.000000   0.000000  0.000000  0.000000   
2016-12-15   0.000000   0.000000  0.000000   0.000000  0.000000  0.000000   
2016-12-16   0.000000   0.000000  0.000000   0.000000  0.000000  0.000000   
...               ...        ...       ...        ...       ...       ...   
2019-07-01  21.637440 -10.264664 -6.588543 -16.289673  1.999794 -2.144251   
2019-07-02  22.255208 -10.264664 -6.588543 -16.289673  1.999794 -2.144251   
2019-07-03  21.637440 -10.264664 -6.588543 -16.289673  1.999794 -2.144251   
2019-07-04  22.255208 -10.264664 -6.588543 -16.289673  1.999794 -2.144251   
2019-07-05  23.490746 -10.264664 -6.588543 -16.2896

In [243]:
compare_results(pricing, bnh, stocks = stocks)

Stock: MQG.AX, -27.8%
Stock: CBA.AX, -11.94%
Stock: NAB.AX, 2.96%
Stock: WBC.AX, -3.77%
Stock: BOQ.AX, 19.63%
Stock: QAN.AX, -65.31%
Stock: VAS.AX, -10.24%
Average result: -13.78%


df_1yr = df[df.index > end - dt.timedelta(days = 760)]
df_1yr_norm = norm_df_med(df_1yr, window = 30)
#test = norm_df_sum(df_1yr_norm, rolling = 0.99)
test_90 = norm_df_sum(df_1yr_norm, rolling = 0.90)

cols = plotly.colors.DEFAULT_PLOTLY_COLORS
k=0
fig_norm_comp = make_subplots(rows = 4, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('Bank Stocks','Normalised Stocks, 90', 'Results','Trading'),
                   row_width = [0.5,0.5,0.5,0.5])

for i in df_1yr:
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr.index, y = df_1yr[i], name = i,
                                       legendgroup = i, marker=dict(color=cols[k])), row =1, col = 1)
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = test_90[i], name = i, 
                                       showlegend = False, legendgroup = i, marker=dict(color=cols[k])), row =2, col = 1)    
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = results_df[i], name = i, 
                                       showlegend = False, legendgroup = i, marker=dict(color=cols[k])), row =3, col = 1)
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = trading_df[i], name = i, 
                                       showlegend = False, legendgroup = i, marker=dict(color=cols[k])), row =4, col = 1)
    k += 1
print(sum(finish)/len(finish))
fig_norm_comp.show()


In [241]:
print(trading_df)

               MQG.AX    CBA.AX   NAB.AX    WBC.AX    BOQ.AX     QAN.AX  \
Date                                                                      
2016-12-12   0.000000  0.000000  0.00000  0.000000  0.000000   0.000000   
2016-12-13   0.000000  0.000000  0.00000  0.000000  0.000000   0.000000   
2016-12-14   0.000000  0.000000  0.00000  0.000000  0.000000   0.000000   
2016-12-15   0.000000  0.000000  0.00000  0.000000  0.000000   0.000000   
2016-12-16   0.000000  0.000000  0.00000  0.000000  0.000000   0.000000   
...               ...       ...      ...       ...       ...        ...   
2019-07-01  19.616626  8.839914 -3.47727  4.250539 -2.203429  24.528326   
2019-07-02  19.616626  8.839914 -3.47727  4.250539 -2.203429  24.528326   
2019-07-03  19.616626  8.839914 -3.47727  4.250539 -2.203429  24.528326   
2019-07-04  19.616626  8.839914 -3.47727  4.250539 -2.203429  24.528326   
2019-07-05  19.616626  8.839914 -3.47727  4.250539 -2.203429  24.528326   

              VAS.AX  
D

In [29]:
def norm_df_sum(df, rolling  = 1, n = 365):
    #new_df = df[df.index > end - dt.timedelta(days = n)].copy()
    new_df = pd.DataFrame(index = df.index)
    for i in stocks:
        totals = []
        rolling_sum = 0
        for j in df.index:
            rolling_sum = rolling_sum * rolling + df[i][j] -1
            #print(df[i][j])
            totals.append(rolling_sum)
        new_df[i] = totals
    return new_df
#test = norm_df_sum(df_1yr_norm,rolling = 0.8)
#test.plot()

print(df_1yr['CBA.AX'][df_1yr.index[0]])

In [30]:
def trade_list(df = df, df_price = df_price, start = dt.timedelta(days = 1500), end = dt.datetime.now(), 
               stock = 'CBA.AX', up_thresh = 0.9, low_thresh = 0.25, thresh_window = 180,
              trig_thresh = 20):
    trim_df = df[df.index > end - start]
    trim_df_price = df_price[df_price.index > end - start]
    n_df = (trim_df)

    #print(n_df)
    #n_df['up_bound'].plot()
    #n_df['low_bound']
    new_df = pd.DataFrame(index = n_df.index)
    new_df['price'] = trim_df_price[stock]
    new_df['norm'] = n_df[stock]
    new_df['up_bound'] = df[stock].rolling(thresh_window, min_periods = 0).quantile(up_thresh).copy()
    new_df['low_bound'] = df[stock].rolling(thresh_window, min_periods = 0).quantile(low_thresh).copy()
    
    trade = []
    buy_trig, sell_trig = 0, 0   
    for i in n_df.index:
        if n_df[stock][i] > new_df['up_bound'][i] and sell_trig == 0:
            sell_trig = 1
            trade.append(1)
        elif n_df[stock][i] < new_df['low_bound'][i] and buy_trig == 0:
            buy_trig = 1
            trade.append(-1)
        else:
            trade.append(0)
        
        #Triggers for sell
        if sell_trig < trig_thresh and sell_trig > 0:
            sell_trig += 1
        elif sell_trig == trig_thresh:
            sell_trig = 0
            
        #Triggers for buy
        if buy_trig < trig_thresh and buy_trig > 0:
            buy_trig += 1
        elif buy_trig == trig_thresh:
            buy_trig = 0 
            
    new_df['trade'] = trade
    return new_df
'''
a = trade_list(df, stock = 'BOQ.AX', start = dt.timedelta(days = 365))
print(len(a))
a['trade'].plot()'''

"\na = trade_list(df, stock = 'BOQ.AX', start = dt.timedelta(days = 365))\nprint(len(a))\na['trade'].plot()"

def trade_list(df = df, df_price = df_price, start = dt.timedelta(days = 365), end = dt.datetime.now(), 
               stock = 'CBA.AX', up_thresh = 1.15, low_thresh = 0.85,
              trig_thresh = 20):
    #print(stock)
    #bound = 0.1
    #up_thresh = 1 + bound
    #low_thresh = 1 - bound
    # Pull data and trim the legnth using 'start' and 'end'
    trim_df = df[df.index > end - start]
    trim_df_price = df_price[df_price.index > end - start]
    # Normalise Data
    n_df = norm_df_med(trim_df)
    new_df = pd.DataFrame(index = n_df.index)
    new_df['price'] = trim_df_price[stock]
    new_df['norm'] = n_df[stock]
    
    trade = []
    buy_trig, sell_trig = 0, 0   
    for i in n_df.index:
        if n_df[stock][i] > up_thresh and sell_trig == 0:
            sell_trig = 1
            trade.append(1)
        elif n_df[stock][i] < low_thresh and buy_trig == 0:
            buy_trig = 1
            trade.append(-1)
        else:
            trade.append(0)
        
        #Triggers for sell
        if sell_trig < trig_thresh and sell_trig > 0:
            sell_trig += 1
        elif sell_trig == trig_thresh:
            sell_trig = 0
            
        #Triggers for buy
        if buy_trig < trig_thresh and buy_trig > 0:
            buy_trig += 1
        elif buy_trig == trig_thresh:
            buy_trig = 0 
            
    new_df['trade'] = trade
    return new_df
'''
a = trade_list(df, stock = 'BOQ.AX', start = dt.timedelta(days = 365))
print(len(a))
a['trade'].plot()'''

In [68]:
def trading_results(df, amount_per_trade = 8000, bank = 20000, brokerage_fee = 20):
    holding_stocks = 0
    total_value = []
    for i in df.index:
        if (df['trade'][i] == -1) & (bank >= amount_per_trade):
            # print('buy')
            bank += -amount_per_trade
            holding_stocks += (amount_per_trade - brokerage_fee) / df['price'][i]
        elif (df['trade'][i] == 1) and (holding_stocks > 0):
            # print('sell')
            bank += holding_stocks * df['price'][i] - brokerage_fee
            holding_stocks = 0
        total_value.append(bank)
    total_value[-1] = bank + holding_stocks * int(df['price'][-1])
    df['value'] = total_value
    return df
#trading_results(a)['value'].plot()

a = trade_list(df, stock = 'NAB.AX', start = dt.timedelta(days = 365))
trading_results(a)['value'].plot()

In [409]:
fig_test = make_subplots(rows = 1, cols = 1)
finish = []
sd_df = norm_df_mean(df, window = 30)
for i in stocks:
    a = trade_list(sd_df,df_price = df_price, stock = i, start = dt.timedelta(days = 365), 
                  )
    results = trading_results(a)
    finish.append(((results['value'][-1]/20000)-1)*100)
    fig_test.add_trace(go.Scatter(x=a.index, y = ((results['value']/20000)-1)*100,  name = i), row =1, col = 1)
#fig_test.show()
print(finish)
print(sum(finish)/len(finish))
print(a)
#a['low_bound'].plot()

[-25.56272558207242, -1.3481754923096334, 3.4862993740140125, -22.46191120011597, -19.320223079112985, -30.14035032061031, -17.70906449313545]
-16.150878684763253
            price      norm  up_bound  low_bound  trade         value
Date                                                                 
2021-12-24   8.13  1.019862  1.036889   0.980009      0  20000.000000
2021-12-29   8.23  1.033530  1.036889   0.980009      0  20000.000000
2021-12-30   8.20  1.030885  1.036889   0.980009      0  20000.000000
2021-12-31   8.09  1.018250  1.034887   0.980009      0  20000.000000
2022-01-04   8.32  1.046760  1.034887   0.980009      1  20000.000000
...           ...       ...       ...        ...    ...           ...
2022-12-15   6.92  0.960489  1.064937   0.957574      0  16458.187101
2022-12-16   6.80  0.945977  1.064937   0.956672      0  16458.187101
2022-12-19   6.82  0.950523  1.064937   0.955172      0  16458.187101
2022-12-20   6.77  0.945883  1.064937   0.954861      0  16458.1871

In [413]:
#a['up_bound'].plot()

In [410]:
fig_test.update_layout(
    title = 'Trading Data',
    xaxis_tickfont_size = 12,
    yaxis = dict(
        title = 'Percentage Gain',
        title_font_size = 14,
        tickfont_size = 12),
    autosize = False,
    width = 800,
    height = 500,
    margin = dict(l = 50, r = 50, b = 100, t = 100, pad =5),
    paper_bgcolor = 'aliceblue'
)

## Graphing Multiple graphs

In [187]:
print(new_df)

              CBA.AX    NAB.AX    WBC.AX    ANZ.AX    MQG.AX    BOQ.AX  \
Date                                                                     
2015-01-01  1.000000  1.000000  1.000000  1.000000  1.000000  1.000000   
2015-01-04  1.001223  1.000744  0.998344  0.999068  0.998974  0.998769   
2015-01-05  0.994868  0.993445  0.991255  0.987877  0.977063  0.977814   
2015-01-06  0.995206  0.997910  0.990156  0.992025  0.991367  0.990460   
2015-01-07  1.000000  1.004768  0.998175  1.000000  1.000000  1.000000   
...              ...       ...       ...       ...       ...       ...   
2022-12-11  0.995231  0.965153  0.981513  0.956716  0.965436  0.947586   
2022-12-12  1.005147  0.984965  0.995582  0.981270  0.973092  0.966184   
2022-12-13  1.007444  0.982877  0.992003  0.979001  0.980691  0.967519   
2022-12-14  1.003382  0.989078  0.989265  0.977505  0.966505  0.957123   
2022-12-15  1.003194  0.992745  0.990099  0.979910  0.966505  0.957785   

             A200.AX  
Date          

In [17]:
import datetime as dt
import pandas as pd
from pandas_datareader import data as pdr
import plotly.offline as pyo
import plotly.graph_objects as go
from plotly.subplots import make_subplots

pyo.init_notebook_mode(connected=True)

In [107]:
end = dt.datetime.now()
start = dt.datetime(2015,1,1)

df = yf.Ticker('CBA.AX', start,end)
df.head

[*********************100%***********************]  1 of 1 completed


<bound method NDFrame.head of                   Open        High         Low       Close   Adj Close  \
Date                                                                     
2015-01-02   84.959686   85.277962   84.661308   85.277962   58.036251   
2015-01-05   85.238182   85.775269   85.049202   85.486832   58.178394   
2015-01-06   84.641411   85.337639   84.412651   84.840332   57.738411   
2015-01-07   84.850281   85.029312   84.094376   84.651360   57.609806   
2015-01-08   85.079041   85.188446   84.671249   84.929848   57.799339   
...                ...         ...         ...         ...         ...   
2022-12-14  106.620003  107.059998  105.839996  106.919998  106.919998   
2022-12-15  106.699997  107.690002  106.220001  106.800003  106.800003   
2022-12-16  106.059998  106.290001  105.160004  105.980003  105.980003   
2022-12-19  105.000000  105.760002  104.750000  105.629997  105.629997   
2022-12-20  105.809998  106.110001  104.930000  105.330002  105.330002   

       

In [108]:
df['MA50'] = df['Close'].rolling(window = 50, min_periods = 0).mean()
df['MA200'] = df['Close'].rolling(window = 200, min_periods = 0).mean()

df['ME30'] = df['Close'].rolling(window = 30, min_periods = 0).median()


In [109]:
fig = make_subplots(rows = 2, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('CBA','Volume'),
                   row_width = [0.2,0.7])

In [110]:
fig.add_trace(go.Candlestick(x = df.index, open= df['Open'], high = df['High'], low = df['Low'], close = df['Close'], 
                             name = 'OHLC'
                            ),row = 1, col = 1)
1

1

In [111]:
fig.add_trace(go.Scatter(x=df.index, y = df['MA50'], marker_color = 'grey', name = 'MA50'), row =1, col = 1)
fig.add_trace(go.Scatter(x=df.index, y = df['MA200'], marker_color = 'lightgrey', name = 'MA200'), row =1, col = 1)
fig.add_trace(go.Scatter(x=df.index, y = df['ME30'], marker_color = 'blue', name = 'ME30'), row =1, col = 1)
1

1

In [112]:
fig.add_trace(go.Bar(x = df.index, y = df['Volume'], marker_color = 'red', showlegend = False), row = 2, col = 1)
1

1

In [113]:
fig.update_layout(
    title = 'CBA historical price chart',
    xaxis_tickfont_size = 12,
    yaxis = dict(
        title = 'Price ($/share)',
        title_font_size = 14,
        tickfont_size = 12),
    autosize = False,
    width = 800,
    height = 500,
    margin = dict(l = 50, r = 50, b = 100, t = 100, pad =5),
    paper_bgcolor = 'aliceblue'
)
1

1

In [114]:
fig.update(layout_xaxis_rangeslider_visible = False)

In [31]:
fig_test = make_subplots(rows = 2, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('CBA','Volume'),
                   row_width = [0.2,0.7])

In [216]:
a=[3,90,3,7,8,100]
if [sum(a)<100]:
    a.append(2)
print(a)

[3, 90, 3, 7, 8, 100, 2]


In [217]:
a=[3,90,3,7,8,100]
if sum(a)<100:
    a.append(2)
print(a)

[3, 90, 3, 7, 8, 100]
